In [45]:
import pandas as pd
import numpy as np
import re
from nltk.corpus import stopwords
import unidecode
import spacy

from happytransformer import HappyTextToText
from happytransformer import TTSettings
from langdetect import detect

In [46]:
top = pd.read_csv('top200.csv')

In [47]:
def chorus(df):
    df['chorus'] = ''
    i = 0
    for morceau in df['lyrics']:
        split = str(morceau).split("Refrain")
        if len(split) == 1:
            split = str(morceau).split("Chorus")
        if len(split) == 1:
            df['chorus'][i] = ''
        else:
            chorus_and_co = split[1].split('] ')
            if len(chorus_and_co) == 1:
                df['chorus'][i] = ''
            else:
                chorus = chorus_and_co[1].split(' [')
                df['chorus'][i] = chorus[0]
        i+=1
    return df

In [48]:
top = chorus(top)

C:\Users\bapti\AppData\Local\Temp\ipykernel_26156\1816682452.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['chorus'][i] = chorus[0]
C:\Users\bapti\AppData\Local\Temp\ipykernel_26156\1816682452.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['chorus'][i] = ''


In [49]:
top_chorus = top['lyrics']

In [50]:
def text_cleaning_fr(text):
    text = unidecode.unidecode(text)
    text = re.sub(r'\[.*?\]', '', text)
    text = re.sub(r"""[.,(/"?:)!;\\]""", '', text)
    text = text.replace("'", ' ')
    text = text.replace("-", ' ')
    cut_words = [' j ', ' J ', ' t ', ' T ', ' m ', ' M ']
    for cw in cut_words:
        text = text.replace(cw, ' '+cw.replace(' ','')+'e ')
    text = text.replace('  ', ' ')
    return text

In [51]:
def text_cleaning_en(text):
    text = unidecode.unidecode(text)
    text = re.sub(r"""[.,(/"?:)!;\\]""", '', text)
    text = text.replace("'", ' ')
    text = text.replace("-", ' ')
    text = text.replace(" re ", ' are ')
    text = text.replace(" s ", ' is ')
    text = text.replace(" m ", ' am ')
    text = text.replace(" t ", ' not ')
    text = text.replace('  ', ' ')
    text = text.lower()
    text = text.split(' ')
    return text

In [52]:
happy_tt = HappyTextToText("MARIAN", "Helsinki-NLP/opus-mt-fr-en")
args = TTSettings(min_length=2)

c:\Users\bapti\AppData\Local\Programs\Python\Python310\lib\site-packages\transformers\models\marian\tokenization_marian.py:194: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")
12/02/2022 15:07:41 - INFO - happytransformer.happy_transformer -   Using model: cpu


In [53]:
def text_translation(text):
    try:
        lang = detect(text)
    except:
        lang = "error"
    if lang == "fr":
        #translate
        final_trans_text = ""
        ran = round(len(text.split())/50)
        if ran == 0:
            trans_text = happy_tt.generate_text(text, args=args)
            final_trans_text = trans_text.text
        else:
            for i in range(ran):
                piece_of_text = ' '.join(text.split()[i*50:50+(i*50)])                
                trans_text = happy_tt.generate_text(piece_of_text, args=args)
                final_trans_text = final_trans_text + " " + trans_text.text
        
    elif lang == "en":
        final_trans_text = text
    else:
        #classify the email as autre
        final_trans_text = text
    return final_trans_text

In [54]:
def stop_words_english(text):
    stop_words = stopwords.words('english')
    stop_words.extend(['eh', 'oh', 'ah', 'yeah', 'ooh'])
    text = [word for word in text if word not in stop_words and len(word)>1]
    return text

In [55]:
def lemmatization(nlp, texte):
    i = 0
    # On regarde chaque mot dans le texte
    # Chaque mot a le numéro i
    for mot in texte:
        # on va lemmatizer
        doc = nlp(mot)
        for token in doc:
            texte[i] = token.lemma_.lower()
            
        i += 1
    
            
    return texte

In [56]:
def data_cleaning(texts):
    
    nlp_en = spacy.load('en_core_web_md')
    
    texts1 = []

    for i in texts.index:

        print(i)

        text1 = text_cleaning_fr(texts[i])

        text1 = text_translation(text1)

        text1 = text_cleaning_en(text1)
            
            #stop words cleaning for object
        text1 = stop_words_english(text1)

        text1 = lemmatization(nlp_en, text1)

        texts1.append(text1)

    return texts1

In [57]:
top_chorus = top_chorus.fillna("vide")

In [58]:
top_chorus = data_cleaning(top_chorus)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [59]:
top_chorus

[['alonz',
  'shk',
  'shk',
  'nap',
  'mame',
  'eheh',
  'ni',
  'mame',
  'eye',
  'bigo',
  'bebe',
  'come',
  'home',
  'late',
  'loading',
  'motorcycle',
  'helmet',
  'mom',
  'know',
  'want',
  'bobby',
  'mom',
  'age',
  'fighting',
  'to',
  'park',
  'play',
  'violin',
  'know',
  'violent',
  'biff',
  'play',
  'violin',
  'play',
  'violin',
  'complicate',
  'stop',
  'soon',
  'heart',
  'black',
  'like',
  'viano',
  'yes',
  'raise',
  'flash',
  'health',
  'hot',
  'give',
  'heart',
  'bobo',
  'yes',
  'even',
  'tarpin',
  'zehef',
  'photo',
  'everything',
  'fine',
  'hey',
  'pilotis',
  'cocktail',
  'co',
  'co',
  'co',
  'co',
  'listen',
  'omah',
  'lay',
  'sing',
  'lo',
  'lo',
  'yes',
  'uh',
  'want',
  'know',
  'budget',
  'life',
  'still',
  'sluggish',
  'different',
  'varia',
  'end',
  'ball',
  'count',
  'friend',
  'versace',
  'go',
  'take',
  'tell',
  'rope',
  'vicelarde',
  'yesterday',
  'make',
  'chick',
  'snoop',
  'f

In [60]:
topchorus = pd.DataFrame([top_chorus])

In [61]:
topchorus.to_csv('top_lyrics.csv', index=False, encoding='utf-8')

In [64]:
topchorus

0     \
0  [alonz, shk, shk, nap, mame, eheh, ni, mame, e...   

                                                1     \
0  [zeg, track, bitch, spend, night, count, bone,...   

                                                2     \
0  [mala, gangx, bang, bang, grr, grr, bang, bang...   

                                                3     \
0  [pew, grr, pew, pew, pew, pew, skrt, rah, rah,...   

                                                4     \
0  [sunt, fericit, can, mananc, un, pepene, un, p...   

                                                5     \
0  [try, write, great, thing, word, try, great, t...   

                                                6     \
0  [mehsah, mehsah, prod, mehsah, prod, prod, kno...   

                                                7     \
0  [amazing, happen, mala, gangx, noxious, timal,...   

                                                8     \
0  [come, harry, wanna, say, goodnight, holdin, b...   

                                                9     ...  \
0  [always, top, deaf, face, jealousy, back, futu...  ...   

                                                1310  \
0  [parte, nask, triplenbeat, la, strada, stancan...   

                                                1311    1312  \
0  [city, tour, helmet, arai, hour, matte, news, ...  [vide]   

                                                1313    1314  \
0  [universe, billion, live, earth, seven, billio...  [vide]   

                                                1315  \
0  [think, feel, different, playin, wembley, eigh...   

                                                1316  \
0  [traphouse, mob, huh, roll, another, one, say,...   

                                                1317  \
0  [want, carry, arm, big, arm, jean, claude, van...   

                                                1318  \
0  [muerte, muerte, davy, one, come, gg, burbe, b...   

                                                1319  
0  [mmh, mmh, mmh, mmh, joe, dwet, file, ouh, hey...  

[1 rows x 1320 columns]

In [63]:
topchorus[0][0]

['alonz',
 'shk',
 'shk',
 'nap',
 'mame',
 'eheh',
 'ni',
 'mame',
 'eye',
 'bigo',
 'bebe',
 'come',
 'home',
 'late',
 'loading',
 'motorcycle',
 'helmet',
 'mom',
 'know',
 'want',
 'bobby',
 'mom',
 'age',
 'fighting',
 'to',
 'park',
 'play',
 'violin',
 'know',
 'violent',
 'biff',
 'play',
 'violin',
 'play',
 'violin',
 'complicate',
 'stop',
 'soon',
 'heart',
 'black',
 'like',
 'viano',
 'yes',
 'raise',
 'flash',
 'health',
 'hot',
 'give',
 'heart',
 'bobo',
 'yes',
 'even',
 'tarpin',
 'zehef',
 'photo',
 'everything',
 'fine',
 'hey',
 'pilotis',
 'cocktail',
 'co',
 'co',
 'co',
 'co',
 'listen',
 'omah',
 'lay',
 'sing',
 'lo',
 'lo',
 'yes',
 'uh',
 'want',
 'know',
 'budget',
 'life',
 'still',
 'sluggish',
 'different',
 'varia',
 'end',
 'ball',
 'count',
 'friend',
 'versace',
 'go',
 'take',
 'tell',
 'rope',
 'vicelarde',
 'yesterday',
 'make',
 'chick',
 'snoop',
 'fe',
 'fe',
 'complicate',
 'stop',
 'soon',
 'health',
 'hot',
 'dear',
 'want',
 'yve',
 'sain

In [68]:
import pandas as pd
import numpy as np
topchorus = pd.read_csv('top_lyrics.csv')
topchorus

0  \
0  ['alonz', 'shk', 'shk', 'nap', 'mame', 'eheh',...   

                                                   1  \
0  ['zeg', 'track', 'bitch', 'spend', 'night', 'c...   

                                                   2  \
0  ['mala', 'gangx', 'bang', 'bang', 'grr', 'grr'...   

                                                   3  \
0  ['pew', 'grr', 'pew', 'pew', 'pew', 'pew', 'sk...   

                                                   4  \
0  ['sunt', 'fericit', 'can', 'mananc', 'un', 'pe...   

                                                   5  \
0  ['try', 'write', 'great', 'thing', 'word', 'tr...   

                                                   6  \
0  ['mehsah', 'mehsah', 'prod', 'mehsah', 'prod',...   

                                                   7  \
0  ['amazing', 'happen', 'mala', 'gangx', 'noxiou...   

                                                   8  \
0  ['come', 'harry', 'wanna', 'say', 'goodnight',...   

                                                   9  ...  \
0  ['always', 'top', 'deaf', 'face', 'jealousy', ...  ...   

                                                1310  \
0  ['parte', 'nask', 'triplenbeat', 'la', 'strada...   

                                                1311      1312  \
0  ['city', 'tour', 'helmet', 'arai', 'hour', 'ma...  ['vide']   

                                                1313      1314  \
0  ['universe', 'billion', 'live', 'earth', 'seve...  ['vide']   

                                                1315  \
0  ['think', 'feel', 'different', 'playin', 'wemb...   

                                                1316  \
0  ['traphouse', 'mob', 'huh', 'roll', 'another',...   

                                                1317  \
0  ['want', 'carry', 'arm', 'big', 'arm', 'jean',...   

                                                1318  \
0  ['muerte', 'muerte', 'davy', 'one', 'come', 'g...   

                                                1319  
0  ['mmh', 'mmh', 'mmh', 'mmh', 'joe', 'dwet', 'f...  

[1 rows x 1320 columns]

In [69]:
for i in topchorus:
    text = topchorus.loc[0][i]
    carac = ['"', '[', ']', "'", " "]
    for c in carac:
        text = text.replace(c, "")
    text = text.split(",")
    topchorus.loc[0][i] = text

In [70]:
topchorus.loc[0][0]

['alonz',
 'shk',
 'shk',
 'nap',
 'mame',
 'eheh',
 'ni',
 'mame',
 'eye',
 'bigo',
 'bebe',
 'come',
 'home',
 'late',
 'loading',
 'motorcycle',
 'helmet',
 'mom',
 'know',
 'want',
 'bobby',
 'mom',
 'age',
 'fighting',
 'to',
 'park',
 'play',
 'violin',
 'know',
 'violent',
 'biff',
 'play',
 'violin',
 'play',
 'violin',
 'complicate',
 'stop',
 'soon',
 'heart',
 'black',
 'like',
 'viano',
 'yes',
 'raise',
 'flash',
 'health',
 'hot',
 'give',
 'heart',
 'bobo',
 'yes',
 'even',
 'tarpin',
 'zehef',
 'photo',
 'everything',
 'fine',
 'hey',
 'pilotis',
 'cocktail',
 'co',
 'co',
 'co',
 'co',
 'listen',
 'omah',
 'lay',
 'sing',
 'lo',
 'lo',
 'yes',
 'uh',
 'want',
 'know',
 'budget',
 'life',
 'still',
 'sluggish',
 'different',
 'varia',
 'end',
 'ball',
 'count',
 'friend',
 'versace',
 'go',
 'take',
 'tell',
 'rope',
 'vicelarde',
 'yesterday',
 'make',
 'chick',
 'snoop',
 'fe',
 'fe',
 'complicate',
 'stop',
 'soon',
 'health',
 'hot',
 'dear',
 'want',
 'yve',
 'sain

In [71]:
data_words = topchorus.loc[0]
data_wordss = [words for words in data_words if words != "" and words != [] and words != 'nan']

In [84]:
i = 0
while i<len(data_wordss):
    data_wordss[i] = [word for word in data_wordss[i] if len(word)>2]
    i+=1

In [85]:
data_wordss[0]

['alonz',
 'shk',
 'shk',
 'nap',
 'mame',
 'eheh',
 'mame',
 'eye',
 'bigo',
 'bebe',
 'come',
 'home',
 'late',
 'loading',
 'motorcycle',
 'helmet',
 'mom',
 'know',
 'want',
 'bobby',
 'mom',
 'age',
 'fighting',
 'park',
 'play',
 'violin',
 'know',
 'violent',
 'biff',
 'play',
 'violin',
 'play',
 'violin',
 'complicate',
 'stop',
 'soon',
 'heart',
 'black',
 'like',
 'viano',
 'yes',
 'raise',
 'flash',
 'health',
 'hot',
 'give',
 'heart',
 'bobo',
 'yes',
 'even',
 'tarpin',
 'zehef',
 'photo',
 'everything',
 'fine',
 'hey',
 'pilotis',
 'cocktail',
 'listen',
 'omah',
 'lay',
 'sing',
 'yes',
 'want',
 'know',
 'budget',
 'life',
 'still',
 'sluggish',
 'different',
 'varia',
 'end',
 'ball',
 'count',
 'friend',
 'versace',
 'take',
 'tell',
 'rope',
 'vicelarde',
 'yesterday',
 'make',
 'chick',
 'snoop',
 'complicate',
 'stop',
 'soon',
 'health',
 'hot',
 'dear',
 'want',
 'yve',
 'saint',
 'lau',
 'lau',
 'give',
 'heart',
 'bobo',
 'yes',
 'meme',
 'tarpin',
 'zehef'

In [86]:
import gensim.corpora as corpora
# Create Dictionary
id2word = corpora.Dictionary(data_wordss)
# Create Corpus
texts = data_wordss
# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]
# View
print(corpus[:1][0][:30])

[(0, 1), (1, 1), (2, 1), (3, 1), (4, 2), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 3), (11, 1), (12, 1), (13, 1), (14, 2), (15, 1), (16, 2), (17, 1), (18, 1), (19, 1), (20, 1), (21, 2), (22, 1), (23, 1), (24, 2), (25, 1), (26, 1), (27, 2), (28, 4), (29, 1)]


In [87]:
document_num = 0
bow_doc_x = corpus[document_num]

for i in range(len(bow_doc_x)):
    print("Word {} (“{}”) appears {} time.".format(bow_doc_x[i][0],
    id2word[bow_doc_x[i][0]],
    bow_doc_x[i][1]))

Word 0 (“age”) appears 1 time.
Word 1 (“alonz”) appears 1 time.
Word 2 (“ball”) appears 1 time.
Word 3 (“bebe”) appears 1 time.
Word 4 (“bed”) appears 2 time.
Word 5 (“biff”) appears 1 time.
Word 6 (“bigo”) appears 1 time.
Word 7 (“bit”) appears 1 time.
Word 8 (“black”) appears 1 time.
Word 9 (“bobby”) appears 1 time.
Word 10 (“bobo”) appears 3 time.
Word 11 (“budget”) appears 1 time.
Word 12 (“certify”) appears 1 time.
Word 13 (“chick”) appears 1 time.
Word 14 (“cocktail”) appears 2 time.
Word 15 (“come”) appears 1 time.
Word 16 (“complicate”) appears 2 time.
Word 17 (“cook”) appears 1 time.
Word 18 (“count”) appears 1 time.
Word 19 (“crypt”) appears 1 time.
Word 20 (“crystal”) appears 1 time.
Word 21 (“dear”) appears 2 time.
Word 22 (“different”) appears 1 time.
Word 23 (“dish”) appears 1 time.
Word 24 (“drop”) appears 2 time.
Word 25 (“eheh”) appears 1 time.
Word 26 (“end”) appears 1 time.
Word 27 (“even”) appears 2 time.
Word 28 (“everything”) appears 4 time.
Word 29 (“eye”) appear

In [93]:
import gensim
lda_model = gensim.models.LdaMulticore(corpus, 
 num_topics = 5, 
 id2word = id2word, 
 passes = 10,
 workers = 2)

In [94]:
for idx, topic in lda_model.print_topics(-1):
    print("Topic: {} \n Words: {}".format(idx, topic))
    print('\n')

Topic: 0 
 Words: 0.018*"like" + 0.011*"get" + 0.010*"make" + 0.009*"want" + 0.008*"love" + 0.008*"know" + 0.007*"see" + 0.007*"say" + 0.006*"life" + 0.006*"heart"


Topic: 1 
 Words: 0.018*"like" + 0.013*"make" + 0.012*"get" + 0.010*"know" + 0.010*"want" + 0.007*"one" + 0.006*"see" + 0.006*"put" + 0.006*"nothing" + 0.005*"love"


Topic: 2 
 Words: 0.015*"hey" + 0.014*"want" + 0.012*"like" + 0.010*"love" + 0.009*"fuck" + 0.009*"get" + 0.007*"make" + 0.007*"que" + 0.007*"know" + 0.007*"see"


Topic: 3 
 Words: 0.023*"know" + 0.014*"get" + 0.011*"like" + 0.011*"want" + 0.010*"make" + 0.010*"see" + 0.009*"love" + 0.008*"let" + 0.007*"good" + 0.007*"one"


Topic: 4 
 Words: 0.014*"make" + 0.013*"like" + 0.012*"want" + 0.010*"time" + 0.009*"big" + 0.009*"know" + 0.008*"love" + 0.008*"get" + 0.007*"take" + 0.007*"see"




In [95]:
import pyLDAvis.gensim_models as gensimvis
import pyLDAvis
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, dictionary=lda_model.id2word)
vis

c:\Users\bapti\AppData\Local\Programs\Python\Python310\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  by='saliency', ascending=False).head(R).drop('saliency', 1)


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3      0.015948 -0.021331       1        1  28.259044
1      0.001896 -0.036179       2        1  24.084987
4     -0.003090 -0.066838       3        1  16.699299
2     -0.096370  0.055884       4        1  15.511768
0      0.081616  0.068464       5        1  15.444901, topic_info=      Term         Freq        Total Category  logprob  loglift
41     hey  1192.000000  1192.000000  Default  30.0000  30.0000
1707   que   312.000000   312.000000  Default  29.0000  29.0000
2279   bam   197.000000   197.000000  Default  28.0000  28.0000
77    seal   261.000000   261.000000  Default  27.0000  27.0000
312    big   959.000000   959.000000  Default  26.0000  26.0000
...    ...          ...          ...      ...      ...      ...
340   fuck   129.420251  1136.108674   Topic5  -5.6706  -0.3044
553    man   108.564514   498.728038   Topic5  -5.8463   0.3432
374    one   119.875789  1395.952162   Topic5  -5.7472  -0.5870
87    tell   114.839974  1221.916418   Topic5  -5.7901  -0.4967
546    let   108.556696   891.919213   Topic5  -5.8463  -0.2382

[412 rows x 6 columns], token_table=       Topic      Freq    Term
term                          
6703       1  0.898281    22nd
6703       2  0.069099    22nd
13069      2  0.974969  3ayani
2334       1  0.166356     ahh
2334       5  0.831778     ahh
...      ...       ...     ...
99         4  0.156839     yes
99         5  0.105917     yes
13196      1  0.041503     zon
13196      4  0.913066     zon
14591      5  0.939618    zulu

[786 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 2, 5, 3, 1])

In [91]:
def format_topics_sentences(ldamodel=None, corpus=corpus, texts=data_wordss):
    # Init output
    sent_topics_df = pd.DataFrame()

    # Get main topic in each document
    for i, row_list in enumerate(ldamodel[corpus]):
        row = row_list[0] if ldamodel.per_word_topics else row_list            
        # print(row)
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = ", ".join([word for word, prop in wp])
                sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    sent_topics_df.columns = ['Dominant_Topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    contents = pd.Series(texts)
    sent_topics_df = pd.concat([sent_topics_df, contents], axis=1)
    return(sent_topics_df)


df_topic_sents_keywords = format_topics_sentences(ldamodel=lda_model, corpus=corpus, texts=data_wordss)

# Format
df_dominant_topic = df_topic_sents_keywords.reset_index()
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Keywords', 'Text']
df_dominant_topic.head(10)

C:\Users\bapti\AppData\Local\Temp\ipykernel_26156\3058185832.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)


Document_No  Dominant_Topic  Topic_Perc_Contrib  \
0            0               7              0.5721   
1            1               4              0.7762   
2            2               3              0.5216   
3            3               3              0.5601   
4            4               8              0.9947   
5            5               3              0.4942   
6            6               3              0.9982   
7            7               3              0.8433   
8            8               2              0.9882   
9            9               3              0.9943   

                                                         Keywords  \
0      like, want, get, know, make, yaka, feat, take, love, lewis   
1          want, make, like, get, know, big, han, fuck, hey, seal   
2        know, like, make, get, want, see, take, life, tell, time   
3        know, like, make, get, want, see, take, life, tell, time   
4  get, like, time, baby, fuck, need, girl, say, everybody, cause   
5        know, like, make, get, want, see, take, life, tell, time   
6        know, like, make, get, want, see, take, life, tell, time   
7        know, like, make, get, want, see, take, life, tell, time   
8        love, know, one, get, see, want, make, night, like, time   
9        know, like, make, get, want, see, take, life, tell, time   

                                                                                                  Text  
0  [alonz, shk, shk, nap, mame, eheh, mame, eye, bigo, bebe, come, home, late, loading, motorcycle,...  
1  [zeg, track, bitch, spend, night, count, bone, take, anywhere, life, lead, tie, hair, think, tou...  
2  [mala, gangx, bang, bang, grr, grr, bang, bang, guy, sherko, inge, always, bsb, hey, hey, think,...  
3  [pew, grr, pew, pew, pew, pew, skrt, rah, rah, rah, rah, block, khabat, fast, pete, bebe, give, ...  
4  [sunt, fericit, can, mananc, pepene, pepene, sunt, fericit, can, mananc, pepene, pepene, fara, s...  
5  [try, write, great, thing, word, try, great, thing, wait, death, good, bad, love, ever, end, bad...  
6  [mehsah, mehsah, prod, mehsah, prod, prod, know, music, like, drug, take, time, every, contract,...  
7  [amazing, happen, mala, gangx, noxious, timal, grr, ten, minute, ten, minute, sport, money, pile...  
8  [come, harry, wanna, say, goodnight, holdin, back, gravity, holdin, back, want, hold, palm, hand...  
9  [always, top, deaf, face, jealousy, back, future, jefe, jefe, johnny, quality, hell, always, top...

In [92]:
# Display setting to show more characters in column
pd.options.display.max_colwidth = 100

sent_topics_sorteddf_mallet = pd.DataFrame()
sent_topics_outdf_grpd = df_topic_sents_keywords.groupby('Dominant_Topic')

for i, grp in sent_topics_outdf_grpd:
    sent_topics_sorteddf_mallet = pd.concat([sent_topics_sorteddf_mallet, 
                                             grp.sort_values(['Perc_Contribution'], ascending=False).head(1)], 
                                            axis=0)

# Reset Index    
sent_topics_sorteddf_mallet.reset_index(drop=True, inplace=True)

# Format
sent_topics_sorteddf_mallet.columns = ['Topic_Num', "Topic_Perc_Contrib", "Keywords", "Representative Text"]

# Show
sent_topics_sorteddf_mallet.head(10)

Topic_Num  Topic_Perc_Contrib  \
0          0              0.9977   
1          1              0.9982   
2          2              0.9968   
3          3              0.9985   
4          4              0.9974   
5          5              0.9981   
6          6              0.9974   
7          7              0.9991   
8          8              0.9972   
9          9              0.9970   

                                                           Keywords  \
0          han, want, hey, know, like, money, gang, tell, make, get   
1          hey, like, mmh, make, gang, woman, want, black, see, ton   
2          love, know, one, get, see, want, make, night, like, time   
3          know, like, make, get, want, see, take, life, tell, time   
4            want, make, like, get, know, big, han, fuck, hey, seal   
5      bam, hun, love, like, true, dun, want, real, little, nothing   
6  que, jojo, baby, come, lie, follow, yah, christmas, pero, quando   
7        like, want, get, know, make, yaka, feat, take, love, lewis   
8    get, like, time, baby, fuck, need, girl, say, everybody, cause   
9         woah, want, good, like, party, make, get, know, king, big   

                                                                                   Representative Text  
0  [noxious, make, hundred, thousand, yesterday, blu, think, need, rest, today, bluuwuu, mexico, ca...  
1  [naprawde, potrzebujesz, terapii, prawdziwy, czarnuch, nie, potrzebuje, terapii, czym, pierdolis...  
2  [gang, gang, keybee, track, mig, moula, rjack, get, late, egg, run, take, bag, noon, show, hide,...  
3  [buddy, mickey, give, date, paris, forget, specify, fuck, demonstration, fuck, demonstration, so...  
4  [han, han, big, freeze, big, kalash, big, kaaris, big, cash, big, kichta, big, price, plug, trip...  
5  [sortie, janvier, booba, pgp, diplo, boom, bye, bye, niska, eva, fleek, lartiste, heuss, enfoire...  
6  [parte, nask, triplenbeat, strada, stancante, rom, pom, pom, esagerato, strada, stancante, rom, ...  
7  [ten, thousand, hour, haggerty, lewis, mansfield, macklemore, publishing, bmi, ryan, lewis, publ...  
8  [mano, never, heaven, parker, ride, life, hold, cause, baby, might, might, give, bite, sweetest,...  
9  [vibez, another, banger, baby, calm, calm, girl, body, put, heart, lockdown, lockdown, lockdown,...

In [80]:
print(len(id2word))

19832


In [81]:
len(corpus)

1320

In [82]:
tot = 0
i = 1
for c in corpus:
    tot += len(c)
    i+=1
print(tot/i)

106.4996214988645


In [ ]:
from pprint import pprint
import gensim
# number of topics
num_topics = 10
# Build LDA model
lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                       id2word=id2word,
                                       num_topics=num_topics)
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

In [ ]:
import pyLDAvis.gensim_models as gensimvis
import pyLDAvis
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, dictionary=lda_model.id2word)
vis

In [ ]:
# Display setting to show more characters in column
pd.options.display.max_colwidth = 100

sent_topics_sorteddf_mallet = pd.DataFrame()
sent_topics_outdf_grpd = df_topic_sents_keywords.groupby('Dominant_Topic')

for i, grp in sent_topics_outdf_grpd:
    sent_topics_sorteddf_mallet = pd.concat([sent_topics_sorteddf_mallet, 
                                             grp.sort_values(['Perc_Contribution'], ascending=False).head(1)], 
                                            axis=0)

# Reset Index    
sent_topics_sorteddf_mallet.reset_index(drop=True, inplace=True)

# Format
sent_topics_sorteddf_mallet.columns = ['Topic_Num', "Topic_Perc_Contrib", "Keywords", "Representative Text"]

# Show
sent_topics_sorteddf_mallet.head(10)